# Coursera Data Science Capstone Project
## Creating Sales Territories for B2B Restaurant Supplier
### James Cage, July 2019

A (fictional) company that manufactures equipment and supplies for Asian restaurants plans to expand into Georgia in the United States. The company wishes to define territories for its salespeople based on the type of restaurants and location in the state. The company plans to hire five “outside sales” people who will visit potential customers (restaurants) and sell them on the benefits of the company’s products.

Sales territories may overlap geographically but given all factors (including the restaurant’s cuisine) all territories must be unique. A salesperson may cover Chinese restaurants in one part of the state, while another salesperson would cover all other ethnicities (Japanese, Vietnamese, Korean, etc.) in the same area (assuming there are enough customers in this area to justify multiple salespeople).

We will define an efficient method to capture restaurant data from Foursquare, and then use machine learning techniques to create effective sales territories.

For more information about this project, see the project's [final report](https://github.com/JamesDCage/Coursera_Capstone/blob/master/James%20Cage%20Capstone%20Project.pdf).

Venue data in this report appears courtesy of Foursquare.

**Please Note!** This is an entirely fictional scenario designed to demonstrate what I've learned about Pandas, Python, Jupyter Notebooks, Folium, and other technologies. The "company" described here is not based in any way on any real company, in Georgia or elsewhere. 



# Table of Contents
1. [Libraries and Functions](#libraries)  
2. [Requesting Data from Foursquare](#requesting)  
    2.1 [Data Gathering Process](#gathering)  
3. [Data Cleaning](#cleaning)  
    3.1 [Fixing Inaccurate Categories](#fixing)
4. [Visualization](#visualization)  
5. [Analysis](#analysis)  
    5.1 [One-hot Encoding](#onehot)  
    5.2 [Scaling Latitude & Longitude](#scaling)  
6. [Conclusions](#conclusion)  
    6.1 [Scenario](#conclusion)  
    6.2 [Methods](#conclusion)    
    6.3 [Critique and Future Directions](#conclusion)
7. [Acknowledgements](#acknowledgements)

<a name="libraries"></a>
# 1. Libraries and Functions

Referenced by code later in the project.

In [1]:
print("Importing ...")
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

import json # library to handle JSON files

import requests # library to handle requests

import time

# import k-means from clustering stage
from sklearn.cluster import KMeans

# for charts and other plots
import matplotlib.pyplot as plt

# ! pip install folium   # uncomment this line if needed
import folium # map rendering library
from folium import plugins

print("Folium version: ", folium.__version__)

Importing ...
Folium version:  0.9.1


In [0]:
# @hidden cell
# Foursquare information

CLIENT_ID = 'CWCPNAVXDH3TI1BGS4VED4ANSUKEFGHBA4511GRPYPKPNJRD' # your Foursquare ID
CLIENT_SECRET = 'ALMFEYIENSPH3RV3TQB1NGWTKTANVJ5QTHAVZ5B1GRJWIP21' # your Foursquare Secret

In [0]:
# Constants

# Foursquare query information that will be constant during this project
VERSION = '20190214' # Foursquare API version
LIMIT = 120 

# Used to convert latitude and longitude to distances in miles
MILES_PER_LAT = 69    # A degree of latitude is 69 miles. 
MILES_PER_LNG = 50.5  # In Georgia, a degree of longitude averages 50.5 miles

# Create a dictionary to control colors of territorial assignments on maps
color_dict = {
 0: 'yellow',
 1: 'green',
 2: 'purple',
 3: 'red',
 4: 'blue'}  

In [0]:
# define function that extracts the category of the venue
# This function is adapted from Coursera Applied Data Science Capstone class

def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
          
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [0]:
def split_box(box, purpose="number"):
    # Breaks a map "box" (tuple of sw,ne corners) into smaller pieces
    # purpose = "size" - if the size of the box exceeds Foursquare's max size
    # purpose = "number" - if the number of returned results is 100 or more,
    #                      indicating that the query "maxed out"
    
    '''Foursquare limits bounding box requests to no more than 10,000 square 
    kilometers, or 3860 square miles. This is a box a bit larger than 
    60 miles on a side.'''
    
    MAX_SIZE_LENGTH = 60

    MAX_DELTA_LAT = MAX_SIZE_LENGTH/MILES_PER_LAT   # Max difference in latitude 
    MAX_DELTA_LNG = MAX_SIZE_LENGTH/MILES_PER_LNG   # Max difference in longitude 
    
    delta_lat = abs(box[0][0] - box[1][0])
    delta_lng = abs(box[0][1] - box[1][1])
    
    boxes = [] # Will hold 1 or more map boxes
    
    if purpose == "number":  # Splitting box because too many results returned
        lat_divisions = lng_divisions = 2 # Break the box into 4 sub-boxes
        
    elif purpose == "size":  # Splitting because box is too large for Foursquare
        lat_divisions = int(np.ceil(delta_lat/MAX_DELTA_LAT))
        lng_divisions = int(np.ceil(delta_lng/MAX_DELTA_LNG))
        
    else:  
        raise ValueError("This function only supports 'size' and 'number' box splitting")
    
    # Create sub-boxes based on number of lat & lng divisions
    for i in range(lat_divisions):
        for j in range(lng_divisions):
            lat_side = delta_lat / lat_divisions
            lng_side = delta_lng / lng_divisions
            swij = (box[0][0] + i * lat_side, box[0][1] + j * lng_side)
            neij = (swij[0] + lat_side, swij[1] + lng_side)
            boxes.append((swij, neij))            
    
    return boxes   

In [0]:
def query_box(box, codes):
    
    '''Creates a Foursquare URL and returns information as a dataframe'''
    
    print(".", end="") # Indicate activity while performing queries

  # Define the Foursquare URL

  # Foursquare category ID requires comma-separated text string
    code_string = ",".join(codes)    
    
    url = f'https://api.foursquare.com/v2/venues/explore?&client_id={CLIENT_ID}' + \
        f'&client_secret={CLIENT_SECRET}&v={VERSION}&sw={box[0][0]},{box[0][1]}' + \
        f'&ne={box[1][0]},{box[1][1]}' + \
        f'&categoryId={code_string}&limit={LIMIT}'
  
  # submit the url and capture the returned text
    venues = requests.get(url).json()["response"]['groups'][0]['items']
  
  # if any venues are captured, process and return dataframe. Otherwise, return None. 
    if venues:
        venues = json_normalize(venues) # flatten JSON

        # select desired columns
        filtered_columns = ['venue.name', 'venue.categories', # 'venue.location.postalCode', 
                        'venue.location.lat', 'venue.location.lng', 'venue.location.state']
        venues = venues.loc[:, filtered_columns]

        # filter the category for each row
        venues['venue.categories'] = venues.apply(get_category_type, axis=1)

        # clean column names
        venues.columns = [col.split(".")[-1] for col in venues.columns]
  
        return venues
  
    else:
        return None  # no venues in box meet criteria    

In [0]:
def shrink_box(box, codes, venue_list, query_list):
    '''Requests data from Foursquare. If the returned data is less than the
    maximum size, record the results. If the data is at the maximum size, 
    split the box into 4 smaller boxes and try again.'''
    
    # Get venues for box (if any) in Pandas dataframe
    box_results = query_box(box, codes)

    try: # This will succeed if 1 or more venues are returned in box_results
        num_clients = box_results.shape[0]

        if num_clients < 100:  
            # Case where results did not "max out" at 100 returned venues
            venue_list += box_results.values.tolist()
            query_list.append((box, num_clients))

        else:  # This is the case where num_clients > 100
            # Split the current box into 4 smallers boxes
            for sub_box in split_box(box, purpose="number"):
                # Recurse on each smaller box.
                shrink_box(sub_box, codes, venue_list, query_list)

    except: # happens if query returns no results
        query_list.append((box, 0))

    return # venue_list and query_list are mutable, no need to return

In [0]:
def GetVenuesByBox(start_box,  # a tuple containing sw & ne corners of box
                   codes):     # a list of Foursquare category strings
    
    '''Given a bounding box of arbitrary size and any list of categories, produces
    multiple Foursquare request and returns the results and a list showing
    the location of successful requests and number of venues for each one.'''
    
    start_time = time.time()  # Start timer to show elapsed time

    venue_list = []      # list of venus of interest
    query_list = []      # boxes and number of venues in each, for visualization
    
    print('Requests in progress', end='')  # query_box() prints dots to indicate progress
    
    # if the start box is too large, split it into smaller boxes
    for box in split_box(start_box, purpose="size"):
        # List will contain one or more boxes. Obtain venues for each
        shrink_box(box, codes, venue_list, query_list)
        
    # Add venue data to a dataframe    
    venues = pd.DataFrame(venue_list, columns=['name', 'categories', \
                                                  'lat', 'lng', 'state'])
    
    print(f"\n{venues.shape[0]} venues returned from {len(query_list)} successful requests in {(time.time()-start_time):.2f} seconds.")
    return venues, query_list

In [0]:
def ShowTable(df_in, category, column_name):
    '''Display count of each category'''
    df_table = df_in[[category,column_name]].groupby(category).count()\
               .sort_values(by=[column_name], ascending=False)
    df_table.index.names, df_table.columns = ['Category'], ['Number']
    return df_table

In [0]:
def ShowTerritories(df_in):
    '''Display table of territories (denoted by colors)'''

    # Add a column for territory color based on dictionary defined in Constants section
    df_in['color'] = df_in['cluster'].apply(lambda x : color_dict[x])

    df_cross = pd.crosstab(df_in.categories, df_in.color, 
                           margins=True, margins_name="Total")
    column_order = ['yellow', 'purple', 'green', 'red', 'blue', 'Total']
       
    return df_cross[column_order]

<a name="requesting"></a>
# 2. Requesting Data from Foursquare

Foursquare allows you to request data by defining a bounding box using latitude & longitude coordinates. I want to request all Asian (including Indian & Pakistani) restaurants in a box drawn around the state of Georgia. 

There are two problems. First, Foursquare has a size limit (about 10,000 square kilometers). Georgia is much larger. Also, Foursquare will only return 100 venues per request (at least with my account type). My code handles these issues by dividing the box into smaller sub-boxes until all boxes are small enough for Foursquare. Then every time a query on a sub-box returns 100 results, the sub-box is split into 4 pieces and a new query is run on each one. This process repeats until all queries return <100 results. Any queries with 100 results are thrown away to avoid duplication.

Let's begin by drawing a large box around Georgia and requesting data. We will cover parts of the adjacent states but we will drop any rows that aren't in Georgia later.

In [0]:
 # Define the southwest and northeast corners of a box around the state of Georgia

fsw = (30.357851, -85.605165)  # Southwest corner, Georgia USA
fne = (35.000659, -80.839729)  # Northeast corner

In [0]:
# The following venue categories come from Foursquare. Note that each 
# category has sub-categories (for example, "Korean Restaurant" in "Asian").
restaurant_codes =  ['4bf58dd8d48988d142941735',   # Asian Restaurant
                     '4bf58dd8d48988d10f941735',   # Indian Restaurant
                     '52e81612bcbc57f1066b79f8']    # Pakistani Restaurant
# Request the data
df_venues, query_list = GetVenuesByBox((fsw,fne), restaurant_codes)

Requests in progress..........................................................................................................................................................................
4386 venues returned from 135 successful requests in 71.98 seconds.


<a name="gathering"></a>
## 2.1 Data Gathering Process

Let's see how the code split the data request. Each box in the picture below represents a Foursquare query that returned 99 or fewer results. The shade of the box shows the number of returned values (you can click on the box to see the number). This is NOT a picture of the data -- we will see that in much more detail later.

In [59]:
# Center the map on the middle of the bounding box defined above 
center = [(fsw[0]+fne[0])/2, (fsw[1]+fne[1])/2]

# Find the maximum number of venues in any square (to calculate fill opacity)
max_clients = max([query[1] for query in query_list])

# Visualize all queries on a map, with fill color indicating number of restaurants
map_georgia = folium.Map(location=center, zoom_start=6, control_scale=True)

# plugins.ScrollZoomToggler().add_to(map_georgia) # Disables mousewheel scaling but
                                                  # covers up map scale
    
# Display the bounding box for every Foursquare request that returned less than
# the maximium number of results.
for box in query_list:
    sw, ne = box[0][0], box[0][1]
    opacity = box[1]/max_clients   # Clients in this box / max across all boxes          
    folium.Rectangle([sw, ne], 
                     popup=str(box[1]), color="black", opacity=0.99, fill=True, 
                     fill_color='orange', weight = 1, 
                     fill_opacity=(opacity)).add_to(map_georgia)
map_georgia.save('box.html')    
map_georgia

In the picture above you can see we started with a 5x6 grid, for 30 requests, to satisfy the size limit. After throwing away all queries returning 100 results (the max limit), how many successful queries did we end up with?

In [60]:
# Number of queries returning <100 results
len(query_list)

135

To get to a total of 135, boxes were split (135 - 30)/3 = 33 times. Requests that returned the maximum number of results were  thrown away to prevent duplication, meaning 33 queries were wasted. The total number of queries to get my data from Georgia was 135 +  33 = 168. 

However, the smallest boxes cover less than 1 square mile. Georgia is almost 60,000 square miles large. **Over 50,000 queries would be needed to get this data with equal-sized boxes.** So this method is a bit better than that.

It generally takes 50-70 seconds to get the data in this way.

<a name="cleaning"></a>
# 3. Data Cleaning

Now let's look at the data we've obtained, and get rid of any venues we don't need for our analysis.

In [61]:
print("Number of restaurants in data set: ",df_venues.shape[0],"\n\n")
df_venues.head()

Number of restaurants in data set:  4386 




name          categories        lat        lng  \
0  Super Canton Chinese Restaurant  Chinese Restaurant  30.951445 -85.516435   
1                   Fortune Cookie  Chinese Restaurant  30.783262 -85.248280   
2      New Star Chinese Restaurant    Asian Restaurant  30.754914 -85.549341   
3                       King House    Asian Restaurant  30.442998 -85.054370   
4                     Panda Buffet  Chinese Restaurant  30.774442 -85.223421   

  state  
0    FL  
1    FL  
2    FL  
3    FL  
4    FL

My bounding-box approach obtained restaurants in parts of adjacent states. Let's get rid of those.

In [62]:
# Which states are included in the data set?
print(list(set(df_venues.state)))

['South Carolina', 'SC', 'FL', 'TN', 'Georgia', 'GA', 'AL', 'Alabama', 'Florida']


In [63]:
# Get rid of restaurants in other states and count the results.
df_georgia = df_venues[df_venues['state'].isin(['GA', 'Georgia'])]
print("Number of restaurants in Georgia: ",df_georgia.shape[0])

Number of restaurants in Georgia:  3418


That's better. In theory, this approach would prevent duplication in the data set, but I always like to be sure. Let's check for duplicate venues.

In [64]:
print("Before dropping duplicates: ",df_georgia.shape[0])
df_georgia = df_georgia.drop_duplicates(keep='first')
print("After dropping duplicates: ",df_georgia.shape[0])

Before dropping duplicates:  3418
After dropping duplicates:  3418


Foursquare did a good job of giving us a unique data set. I also looked at the data and confirmed that all rows contain values for restaurant name, categories, lat, and lng. Now let's look at the restaurant categories. Did we only get the ones we wanted?

In [65]:
ShowTable(df_georgia,'categories','name')

Number
Category                             
Chinese Restaurant               1063
Asian Restaurant                  666
Japanese Restaurant               453
Indian Restaurant                 250
Sushi Restaurant                  246
Korean Restaurant                 213
Thai Restaurant                   176
Vietnamese Restaurant              93
Noodle House                       32
Grocery Store                      15
Ramen Restaurant                   14
American Restaurant                10
Szechuan Restaurant                 9
Bakery                              9
Restaurant                          8
Supermarket                         8
Seafood Restaurant                  8
Wings Joint                         8
Taiwanese Restaurant                7
North Indian Restaurant             7
Fast Food Restaurant                6
Food Court                          6
Bar                                 6
South Indian Restaurant             6
Indian Chinese Restaurant           5
Malay Restaurant                    5
Pakistani Restaurant                5
Café                                5
Shabu-Shabu Restaurant              4
Indonesian Restaurant               4
Hotpot Restaurant                   4
Cantonese Restaurant                3
Dim Sum Restaurant                  3
Mongolian Restaurant                3
Pizza Place                         3
Chaat Place                         3
BBQ Joint                           3
Poke Place                          3
Dumpling Restaurant                 2
Sandwich Place                      2
Sports Bar                          2
Steakhouse                          2
Vegetarian / Vegan Restaurant       2
Farmers Market                      2
Japanese Curry Restaurant           2
Karaoke Bar                         2
Coffee Shop                         2
Food Truck                          2
Middle Eastern Restaurant           1
Hotel Bar                           1
Filipino Restaurant                 1
Food & Drink Shop                   1
Tea Room                            1
Fried Chicken Joint                 1
Taco Place                          1
Breakfast Spot                      1
Bubble Tea Shop                     1
Buffet                              1
Garden                              1
Gas Station                         1
Snack Place                         1
Soup Place                          1
Mexican Restaurant                  1
Shanghai Restaurant                 1
Hunan Restaurant                    1
Deli / Bodega                       1
Indian Sweet Shop                   1
Salon / Barbershop                  1
Italian Restaurant                  1
Caribbean Restaurant                1
Convenience Store                   1
Jiangsu Restaurant                  1
Cocktail Bar                        1
New American Restaurant             1

Convenience store? Italian restaurant? Garden? American restaurant? Clearly we need to get rid of some of these venues. In the cell below, I go through the list of categories and define a list of ones we want to get rid of. I generated the list using this command:

    sorted(list(set(df_georgia['categories'])))

In many cases, I used a command like the following to see which restaurants were in a suspicious category: 

     df_georgia[df_georgia['categories'].isin(['Taco Place'])]

You can see my comments in the lines below.

In [0]:
# Create a list of categories we DON'T want. 
# List generated using this command: sorted(list(set(df_georgia['categories'])))
# Categories to KEEP are commented OUT

bad_list = ['American Restaurant',
 #'Asian Restaurant',
 #'BBQ Joint',
 'Bakery',
 'Bar',
 'Breakfast Spot',
 #'Bubble Tea Shop',
 #'Buffet', # One, Japanese
 'Café',
 #'Cantonese Restaurant',
 'Caribbean Restaurant',
 #'Chaat Place',
 #'Chinese Restaurant',
 'Cocktail Bar',
 'Coffee Shop',
 'Convenience Store',
 'Deli / Bodega',
 #'Dim Sum Restaurant',
 'Dumpling Restaurant',   # Two restaurants, both Korean, both permanently closed
 'Farmers Market',
 'Fast Food Restaurant',
 #'Filipino Restaurant',
 #'Food & Drink Shop',
 'Food Court',
 #'Food Truck',
 #'Fried Chicken Joint',  # One, Korean
 'Garden',  # One instance. Chinese restaurant.
 'Gas Station',
 'Grocery Store',
 'Hotel Bar',
 #'Hotpot Restaurant',
 #'Hunan Restaurant',
 #'Indian Chinese Restaurant',
 #'Indian Restaurant',
 #'Indian Sweet Shop',
 #'Indonesian Restaurant',
 'Italian Restaurant',
 #'Japanese Curry Restaurant',
 #'Japanese Restaurant',
 #'Jiangsu Restaurant',
 'Karaoke Bar',
 #'Korean Restaurant',
 #'Malay Restaurant',   # Five instances. Roll into "Asian"
 'Mexican Restaurant',
 'Middle Eastern Restaurant',
 #'Mongolian Restaurant', #Roll into "Asian"
 'New American Restaurant',
 #'Noodle House',
 #'North Indian Restaurant',
 #'Pakistani Restaurant',
 'Pizza Place',
 #'Poke Place',  # Hawaiian, but we'll call it Japanese
 #'Ramen Restaurant',
 'Restaurant',
 'Salon / Barbershop',
 'Sandwich Place',
 'Seafood Restaurant',
 #'Shabu-Shabu Restaurant',
 #'Shanghai Restaurant',
 'Snack Place',
 'Soup Place',
 #'South Indian Restaurant',
 'Sports Bar',
 #'Steakhouse', # Two. Both Japanese
 #'Supermarket',  # Four. All have restaurants inside
 #'Sushi Restaurant',
 #'Szechuan Restaurant',
 #'Taco Place',  # One location "Hankook Taqueria" Korean
 #'Taiwanese Restaurant',
 #'Tea Room',  # One Location, Chinese
 #'Thai Restaurant',
 'Vegetarian / Vegan Restaurant',
 #'Vietnamese Restaurant',
 'Wings Joint']


Let's see how many restaurants are in the categories we don't want, and drop them from the data frame.

In [67]:
print("Number of restaurants in unwanted categories (dropped): ", df_georgia[df_georgia['categories'].isin(bad_list)].shape[0])
df_georgia = df_georgia[~df_georgia['categories'].isin(bad_list)]
print("Restaurants remaining in dataset: ", df_georgia.shape[0])

Number of restaurants in unwanted categories (dropped):  113
Restaurants remaining in dataset:  3305


Now let's consolidate some categories. Some of the categories remaining in our database (such as Szechuan Restaurant) are sub-categories. For our purposes, we want to roll these up to the top-level category (Szechuan --> Chinese, for example). Other categories roll up because I looked at the restaurants in the category and found that they all should have been put in another category (for example, all Steakhouses in our database are Japanese). Now I will define lists that will help consolidate categories in these cases.

In [0]:
# Define sub-categories that will be consolidated into major categories.
roll_up = [[['Bubble Tea Shop','Cantonese Restaurant','Dim Sum Restaurant','Garden', \
            'Shanghai Restaurant','Szechuan Restaurant', 'Taiwanese Restaurant', \
            'Tea Room', 'Hunan Restaurant'], 'Chinese Restaurant'],
           [['Buffet','Japanese Curry Restaurant', 'Japanese Restaurant', \
            'Ramen Restaurant', 'Shabu-Shabu Restaurant','Steakhouse', \
            'Sushi Restaurant'], 'Japanese Restaurant'],
           [['Fried Chicken Joint','Hot Dog Joint', 'Taco Place'], 'Korean Restaurant'],
           [['Indian Chinese Restaurant','Indian Restaurant','Jiangsu Restaurant'], \
            'Indo-Pak Restaurant'],
           [['BBQ Joint', 'Filipino Restaurant','Food Truck','Hotpot Restaurant',\
            'Indonesian Restaurant','Karaoke Bar','Malay Restaurant', \
            'Mongolian Restaurant', 'Noodle House','Poke Place', \
            'Sandwich Place', 'Supermarket'], 'Asian Restaurant'],
           [['Indian Restaurant', 'North Indian Restaurant',
             'South Indian Restaurant', 'Indian Chinese Restaurant',
             'Pakistani Restaurant', 'Chaat Place', 'Food & Drink Shop',
             'Gourmet Shop', 'Indian Sweet Shop', 'Tea Room'],'Indo-Pak Restaurant']]

In [69]:
# Consolidate categories
for cat_list in roll_up:
    df_georgia.loc[df_georgia.categories.isin(cat_list[0]), 'categories'] = cat_list[1]
    
ShowTable(df_georgia,'categories','name')

Number
Category                     
Chinese Restaurant       1089
Asian Restaurant          731
Japanese Restaurant       722
Indo-Pak Restaurant       279
Korean Restaurant         215
Thai Restaurant           176
Vietnamese Restaurant      93

Now that we have all the restaurants in one place, let's take a closer look at the data and fix some inaccuracies.

<a name="fixing"></a>
## 3.1 Fixing Inaccurate Categories

After looking through the data, it's clear that the categorization of the restaurants can be improved. For example, there are plenty of restaurants in the general "Asian" category that have "Japanese" or "Chinese" in their names. There are also some restaurants that are just in the wrong category - again, Chinese restaurants that are categorized as Japanese, etc. Let's see if we can fix this programmatically, and with a minimum of manual effort.

I extracted the names of the restaurants in each category, and did a word frequency analysis to find terms that are common and specific to each restaurant type. For example, Vietnamese restaurant names often have these terms:

    vietnamese_terms = ['Pho', 'Saigon', 'Viet', 'Banh Mi']
    
Let's see if we can use those terms to correct some assignment problems in this database.

In [0]:
# Define terms commonly found in restaurant names for each country of origin.

china_terms = ['China', 'Chinese', 'Wok', 'Hong Kong', 'Panda', 'Peking', 
               'Beijing', 'Great Wall']
japan_terms = ['Japanese', 'Tokyo', 'Japan', 'Osaka', 
               'Shogun', 'Fuji', 'Sumo', 'Ichiban', 'Kobe', 'Sakura', 'Ramen', 
               'Teriyaki', 'Ninja', 'Shabu']
korea_terms = ['Korea', 'Gogi']
thailand_terms = ['Thai', 'Bangkok']
vietnam_terms = ['Pho', 'Saigon', 'Viet', 'Banh Mi']
indopak_terms = ['India', 'Bombay', 'Biryani', 'Naan', 'Masala']

term_list = [['Chinese Restaurant',china_terms],
             ['Japanese Restaurant',japan_terms],
             ['Korean Restaurant', korea_terms],
             ['Thai Restaurant', thailand_terms],
             ['Vietnamese Restaurant', vietnam_terms],
             ['Indo-Pak Restaurant', indopak_terms]]

In [0]:
# Use keywords to reassign restaurants into more accurate categories
# Reset index to ensure it is unique and continuous
df_georgia.reset_index(drop=True, inplace = True)
# Iterate through the dataframe
for i in range(df_georgia.shape[0]):
    # For each row, see if any keyword appears in the restaurant name
    # If so, change the category
    for a_term in term_list:
        if any(x in df_georgia.loc[i,'name'] for x in a_term[1]):
            df_georgia.loc[i, 'categories'] = a_term[0]

Our data cleaning is complete. What does the cleaned database look like?

In [72]:
print(df_georgia.shape)
ShowTable(df_georgia,'categories','name')

(3305, 5)


Number
Category                     
Chinese Restaurant       1216
Japanese Restaurant       798
Asian Restaurant          477
Indo-Pak Restaurant       276
Korean Restaurant         215
Thai Restaurant           202
Vietnamese Restaurant     121

Notice that there are fewer 'Asian' restaurants and more restaurants in other categories. Now that we have our data, let's get an idea of where the restaurants are in the state.

<a name="visualization"></a>
# 4. Visualization
Before we create sales territories from the data, let's see where our restaurants are located.


In [73]:

# Center the map on the middle of the bounding box defined above 
center = [(fsw[0]+fne[0])/2, (fsw[1]+fne[1])/2]
map_georgia = folium.Map(location=center, zoom_start=7, control_scale=True)   

heat_data = [[row['lat'],row['lng']] for index, row in df_georgia.iterrows()]
# Create a heatmap of Asian restaurants
plugins.HeatMap(heat_data, radius=15).add_to(map_georgia)

# plugins.ScrollZoomToggler().add_to(map_georgia) # Disables mousewheel scaling but
                                                  # covers up map scale

map_georgia.save('heatmap.html')      
map_georgia

The heatmap shows that bulk of restaurants are in the greater Atlanta area, but it can be difficult to see how the rest of the state stacks up relative to Atlanta. Fortunately, Folium has another way to see the information. Let's use cluster markers. Zoom in for more detail.

In [74]:
# Use cluster markers to show distribution of Asian restaurants in the state.
print(f'Number of Asian restaurants in Georgia: {df_georgia.shape[0]}')

# Center the map on the middle of the bounding box defined above 
center = [(fsw[0]+fne[0])/2, (fsw[1]+fne[1])/2]

map_georgia = folium.Map(location=center, zoom_start=7,  control_scale=True)

# Create Marker Cluster
all_cluster = plugins.MarkerCluster(control=False)
map_georgia.add_child(all_cluster)

sub_group_dict = {}  # For marker cluster sub-groups

# Create a list of categories, ordered by most-to-least popular
category_list = list(df_georgia.groupby('categories').count().sort_values(by=['name'], ascending=False).index)

# Create a sub-group for each type of restaurant
for category in category_list:
    sub_group_dict[category] = plugins.FeatureGroupSubGroup(all_cluster,category)
    map_georgia.add_child(sub_group_dict[category])

# plugins.ScrollZoomToggler().add_to(map_georgia) # Disables mousewheel scaling but
                                                  # covers up map scale

# Assign each restaurant to the appropriate sub-group
for restaurant in df_georgia.iterrows():
    folium.Marker(location = [restaurant[1]['lat'],restaurant[1]['lng']]
                  #, popup=restaurant[1]['name']  # Overloads Folium to add this
                 ).add_to(sub_group_dict[restaurant[1]['categories']])

# Display layer control
folium.LayerControl(collapsed=False).add_to(map_georgia)

map_georgia.save('cluster.html') 
map_georgia

Number of Asian restaurants in Georgia: 3305


This clarifies the picture. Of the roughly 3300 Asian restaurants in the state, over 2400 are in the greater Atlanta area, with a strong concentration in the communities to the northeast along Interstate 85. The category checkboxes allow us to see how the distribution varies by type of restaurant. While all types are concentrated in the population centers around Atlanta, Chinese and Japanese restaurants are more evenly distributed around the state. They are also the most popular categories.

Now let's divide the potential customer base into sales territories for our restaurant supply company.

<a name="analysis"></a>
# 5. Analysis

This project requires segmenting a market both by geographic data (numeric) and by the restaurant’s cuisine (categorical data). Unfortunately, mixing data of different types in a single machine learning is problematic. Categorical data can made numeric (by using one-hot analysis, for example), but how should the machine learning algorithm interpret combining this with X-Y location data? It is easy to imagine the algorithm grouping Indian restaurants that share a common latitude while their longitudes (and hence the physical distance between them) varies widely. 

Perhaps we can get a useful result by just grouping on either restaurant type or location. Let's try type first.


<a name="onehot"></a>
## 5.1 One-hot Encoding

To use the type of restaurant (such as "Korean Restaurant") in an analysis, we must convert the information into numeric values. We do this by creating a new column for each type of entry in the 'categories' column and assigning a value of 1 when the category matches the column. This is called on-hot encoding.

In [75]:
# Create the one-hot dummy columns as a separate dataframe, 
df_georgia.reset_index(drop=True, inplace = True)
df_georgia_dummies = pd.get_dummies(df_georgia['categories'])

# Change the column names to make them a bit easier to display

df_georgia_dummies.columns = ['Asian', 'Chinese', 'Indo-Pak',
       'Japanese', 'Korean', 'Thai','Vietnamese']

df_georgia_dummies.head(2)

Asian  Chinese  Indo-Pak  Japanese  Korean  Thai  Vietnamese
0      1        0         0         0       0     0           0
1      1        0         0         0       0     0           0

Now let's cluster the territories and see the results.

In [76]:
# Set the number of clusters (equal to the number of salespeople). 
kclusters = 5

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(df_georgia_dummies)

# add cluster labels to dataframe and take a look
df_georgia['cluster']=kmeans.labels_
df_georgia.head()

name          categories        lat        lng state  \
0          Yuki Express    Asian Restaurant  30.903404 -84.537571    GA   
1                 Makan    Asian Restaurant  30.903800 -84.575470    GA   
2  Jin's Chinese Buffet  Chinese Restaurant  30.891642 -84.207543    GA   
3     Star China Buffet  Chinese Restaurant  30.902765 -84.554162    GA   
4             No1 China  Chinese Restaurant  30.886484 -84.205227    GA   

   cluster  
0        3  
1        3  
2        2  
3        2  
4        2

Let's assign a color to each cluster to make it easier to understand the sales clusters when displayed both as a crosstab and a map.

In [77]:
# Display sales territories (denoted by colors)
ShowTerritories(df_georgia)

color                  yellow  purple  green  red  blue  Total
categories                                                    
Asian Restaurant            0       0      0  477     0    477
Chinese Restaurant          0    1216      0    0     0   1216
Indo-Pak Restaurant         0       0      0    0   276    276
Japanese Restaurant         0       0    798    0     0    798
Korean Restaurant         215       0      0    0     0    215
Thai Restaurant           202       0      0    0     0    202
Vietnamese Restaurant     121       0      0    0     0    121
Total                     538    1216    798  477   276   3305

In [78]:
# Center the map on the middle of the bounding box defined above 
center = [(fsw[0]+fne[0])/2, (fsw[1]+fne[1])/2]
map_georgia = folium.Map(location=center, zoom_start=7, control_scale=True) 

# Plot results. Skip some rows due to folium performance limits. 
skip_count = 20 # Set as high as possible without crashing Folium. ~20 if local 
               # Jupyter environment, ~7 if not

for restaurant in df_georgia[df_georgia.index % skip_count != 0].iterrows():
    color = color_dict[restaurant[1]['cluster']]
    opacity=0.5
    folium.CircleMarker(radius = 4, color=color, fill_color=color, opacity=opacity, fill_opacity=opacity,
                  location = [restaurant[1]['lat'],restaurant[1]['lng']]).add_to(map_georgia)
map_georgia

Grouping solely on restaurant type produces unwieldy territories. Most sales territories only serve one kind of restaurant, but every territory covers the entire state. Travel time would harm productivity in this case. This analysis also uncovers a charming attribute of k means clustering - its tendency to produce groups of widely different sizes.

Now let's try clustering based on location data

<a name="scaling"></a>
## 5.2 Scaling Latitude & Longitude

A degree of latitude and a degree of longitude represent different distances. A degree of latitude is about 69 miles anywhere in the world. In Georgia, about 50.5 miles separate degrees of longitude. These constants were defined globally in this project (see top of this notebook) and used in my function 'split_box()'. Let's scale latitude and longitude so that a one degree change in either represents the same distance and store the results in X and Y.

In [79]:
# Scale and convert latitude and longitude to consistent X and Y coordinates.

# MILES_PER_LAT and MILES_PER_LNG are defined at the top of this project     
df_georgia['X'] = df_georgia['lat'] * MILES_PER_LAT
df_georgia['Y'] = df_georgia['lng'] * MILES_PER_LNG 
df_georgia.head(2)

name        categories        lat        lng state  cluster color  \
0  Yuki Express  Asian Restaurant  30.903404 -84.537571    GA        3   red   
1         Makan  Asian Restaurant  30.903800 -84.575470    GA        3   red   

             X            Y  
0  2132.334856 -4269.147348  
1  2132.362200 -4271.061235

In [80]:
# Set the number of clusters (equal to the number of salespeople). 
kclusters = 5
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(df_georgia[['X','Y']])

# add cluster labels to dataframe and take a look
df_georgia['cluster']=kmeans.labels_
df_georgia['color'] = df_georgia['cluster'].apply(lambda x : color_dict[x])
df_georgia.head()

name          categories        lat        lng state  \
0          Yuki Express    Asian Restaurant  30.903404 -84.537571    GA   
1                 Makan    Asian Restaurant  30.903800 -84.575470    GA   
2  Jin's Chinese Buffet  Chinese Restaurant  30.891642 -84.207543    GA   
3     Star China Buffet  Chinese Restaurant  30.902765 -84.554162    GA   
4             No1 China  Chinese Restaurant  30.886484 -84.205227    GA   

   cluster   color            X            Y  
0        0  yellow  2132.334856 -4269.147348  
1        0  yellow  2132.362200 -4271.061235  
2        0  yellow  2131.523310 -4252.480924  
3        0  yellow  2132.290771 -4269.985162  
4        0  yellow  2131.167411 -4252.363947

In [81]:
# Display sales territories (denoted by colors)
ShowTerritories(df_georgia)

color                  yellow  purple  green  red  blue  Total
categories                                                    
Asian Restaurant           15      39    386   13    24    477
Chinese Restaurant         52     108    859   69   128   1216
Indo-Pak Restaurant         4       9    250    5     8    276
Japanese Restaurant        42      89    559   39    69    798
Korean Restaurant           0       5    188    6    16    215
Thai Restaurant             5      18    160    4    15    202
Vietnamese Restaurant       1       6    107    1     6    121
Total                     119     274   2509  137   266   3305

In [82]:
# Center the map on the middle of the bounding box defined above 
center = [(fsw[0]+fne[0])/2, (fsw[1]+fne[1])/2]
map_georgia = folium.Map(location=center, zoom_start=7, control_scale=True) 

# Plot results. Skip some rows due to folium performance limits. 
skip_count = 20 # Set as high as possible without crashing Folium

for restaurant in df_georgia[df_georgia.index % skip_count != 0].iterrows():
    color = color_dict[restaurant[1]['cluster']]
    opacity=0.5
    folium.CircleMarker(radius = 4, color=color, fill_color=color, opacity=opacity, fill_opacity=opacity,
                  location = [restaurant[1]['lat'],restaurant[1]['lng']]).add_to(map_georgia)

# Create dataframe showing territorial assignment and map color    
df_cross = ShowTerritories(df_georgia)  

# Display territory name and restaurant count. Show popup on load and do not
# close popups if other popups are opened ("sticky" behaviour)
for color in set(df_georgia.color):
    location=(df_georgia[df_georgia.color == color].lat.mean(),
              df_georgia[df_georgia.color == color].lng.mean())
    pop_text = color.title() + '\n' + str(df_cross.loc['Total',color])
    popup = folium.Popup(html=pop_text, show=True, sticky=True, parse_html=True)
    folium.Marker(location = location,
              icon=folium.Icon(),popup=popup
             ).add_to(map_georgia)
    
map_georgia

Clustering the restaurants physically yields sales territories that include all types of restaurants. This increases the load on the salespeople. However, this grouping does suggest a possible solution. Note that the territories outside of the Atlanta area have relatively few restaurants. These territories could be merged together to form two territories, freeing up two salespeople to move to the Atlanta area.  

The two territories outside of the Atlanta area would be larger and include all types of restaurants, thereby increasing the time the salespeople would spend travelling and learning about the restaurant types. However, the number of restaurants would still be lower than average, helping to balance the load.

Now three salespeople are available to work in the Atlanta area, which can be grouped by restaurant type. These salespeople would have a smaller physical territory to cover and fewer restaurant types to learn about, but more restaurants to cover. 

Let's try this approach. We will merge the two southwestern territories together (to take advantage of I-75). The southeastern territories form our final area.

In [0]:
# Merge clusters 2 and 3
df_georgia.loc[df_georgia.cluster == 2, 'cluster'] = 3

# Merge clusters 0 and 4
df_georgia.loc[df_georgia.cluster == 0, 'cluster'] = 4

Now let's re-cluster the Atlanta area (currently represented by Cluster 1) by restaurant type.

In [0]:
# Separate Cluster 1 from df_georgia
df_atlanta = df_georgia[df_georgia['cluster']==1]

# Create the one-hot dummy columns as a separate dataframe, 
df_atlanta_dummies = pd.get_dummies(df_atlanta['categories'])

# Change the column names to make them a bit easier to display

df_atlanta_dummies.columns = ['Asian', 'Chinese', 'Indo-Pak',
       'Japanese', 'Korean', 'Thai','Vietnamese']

In [0]:
# Set the number of clusters (equal to the number of Atlanta salespeople). 
kclusters = 3

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(df_atlanta_dummies)

# add cluster labels to dataframe and take a look
df_georgia.loc[df_georgia['cluster']==1,'cluster']=kmeans.labels_

In [86]:
# Display sales territories (denoted by colors)
ShowTerritories(df_georgia)

color                  yellow  purple  green  red  blue  Total
categories                                                    
Asian Restaurant          386       0      0   52    39    477
Chinese Restaurant          0       0    859  177   180   1216
Indo-Pak Restaurant       250       0      0   14    12    276
Japanese Restaurant         0     559      0  128   111    798
Korean Restaurant         188       0      0   11    16    215
Thai Restaurant           160       0      0   22    20    202
Vietnamese Restaurant     107       0      0    7     7    121
Total                    1091     559    859  411   385   3305

The Atlanta territories (Yellow, Purple, and Green) are better, but still uneven. Can we rebalance the territories with the smallest and largest number of restaurants? The average should be around 840 restaurants in each territory. The territory consisting only of Chinese restaurants (Green) is very close. We can more evenly balance the other two Atlanta territories (Yellow and Purple) by moving about 270 restaurants from the largest Atlanta territory to the smallest. There are two obvious ways to do this:
1. Move Indo-Pak restaurants, or
2. Move Vietnamese and Thai restaurants

Which is better? Remember that grouping in the Atlanta area was done without taking location data into account. Let's look at the center of mass for each cuisine in these two territories and see if there's an obvious correlation.


In [87]:
# Place markers showing center of each type of restaurant in the North Georgia unequal territories. 

df_ga_north = df_georgia[df_georgia.cluster.isin([0,2])]

# Center the map on the markers 
center = (df_ga_north.lat.mean(),df_ga_north.lng.mean())
map_georgia = folium.Map(location=center, zoom_start=12, control_scale=True) 

# Find the cuisine types in these two territories and place a marker at the average
# location for each.
for category in set(df_ga_north.categories):
    location=(df_ga_north[df_ga_north.categories == category].lat.mean(),
              df_ga_north[df_ga_north.categories == category].lng.mean())
    popup = folium.Popup(html=category, show=True, sticky=True, parse_html=True)
    folium.Marker(location = location,
              icon=folium.Icon(),popup=popup,
             ).add_to(map_georgia)

map_georgia.save('mass.html')    
map_georgia

The "center" of the Indo-Pak restaurants is closer to the Japanese center than are either the Thai or Vietnamese. By this measure, it would make more sense to move Indo-Pak into territory that currently only contains Japanese Restaurants. But notice the scale. The difference is only 3-4 miles in a territory that is about 150 miles across. If we move the Vietnamese and Thai restaurants instead, each territory will include 3 cuisines. Let's take option 2, and look at the results.

In [0]:
# Move Vietnames and Thai restaurants from Cluster 0 to Cluster 2
df_georgia.loc[(df_georgia.cluster == 0) & 
               ((df_georgia.categories == "Thai Restaurant") | 
                (df_georgia.categories == "Vietnamese Restaurant")), 'cluster'] = 2 

In [89]:
# Center the map on the middle of the bounding box defined above 
center = [(fsw[0]+fne[0])/2, (fsw[1]+fne[1])/2]
map_georgia = folium.Map(location=center, zoom_start=7, control_scale=True) 

# Plot results. Skip some rows due to folium performance limits. 
skip_count = 20 # Set as high as possible without crashing Folium

for restaurant in df_georgia[df_georgia.index % skip_count != 0].iterrows():
    color = color_dict[restaurant[1]['cluster']]
    opacity=0.5
    folium.CircleMarker(radius = 4, color=color, fill_color=color, opacity=opacity, fill_opacity=opacity,
                  location = [restaurant[1]['lat'],restaurant[1]['lng']]).add_to(map_georgia)

map_georgia.save('final.html')    
map_georgia

In [90]:
# Display sales territories (denoted by colors)
ShowTerritories(df_georgia)

color                  yellow  purple  green  red  blue  Total
categories                                                    
Asian Restaurant          386       0      0   52    39    477
Chinese Restaurant          0       0    859  177   180   1216
Indo-Pak Restaurant       250       0      0   14    12    276
Japanese Restaurant         0     559      0  128   111    798
Korean Restaurant         188       0      0   11    16    215
Thai Restaurant             0     160      0   22    20    202
Vietnamese Restaurant       0     107      0    7     7    121
Total                     824     826    859  411   385   3305

Our Atlanta-area territories are now balanced in size, number of restaurants, and (to the extent possible) number of cuisines. Our territories are complete!

<a name="conclusion"></a>
# 6. Conclusions

## 6.1 Scenario

This project has satisfied the requirements of the problem statement by creating five mutually-exclusive sales territories. As the company's circumstances change (for example, hiring new salespeople in the future or expanding operations to other states) this analysis can be quickly repeated with new data and constraints. In the meantime, assigning new restaurants to the existing territories is obvious.

## 6.2 Methods

Extracting and cleaning data for this project was a challenge, because Georgia has both large areas with few Asian restaurants and areas of very high restaurant concentrations. The recursive method of requesting data (using bounding box requests with recursion) is efficient, quick, and provides a complete data set with no duplication. 

The data set itself had a fairly high percentage of mistakes, requiring extensive data cleaning. I used programmatic methods wherever possible to reduce labor and to make it possible to replicate the project as circumstances change. While data cleaning is not glamourous, it takes a large part of the time for most data science projects and I gained valuable experience in this area.

This project used machine learning techniques across two different types of data. This required balancing domain knowledge of sales methods and the restaurant industry with the capabilities and restraints of the machine learning technology used (in this case, k means clustering). 

## 6.3 Critique and Future Directions

The final sales territories are clearly defined, which would make it easier for our (fictional) salespeople to identify and pursue opportunities. However, in the densely-populated Atlanta metro area location data was used manually, and not as part of a machine learning algorithm. This was appropriate given the number of clusters (salespeople), but enhancements to this project could include methods to mix location and cuisine data into the same learning algorithm, perhaps using a custom algorithm. The algorithm chosen for this project (k means) tends to produce uneven groupings (particularly in cases where there are uneven concentrations of samples), and this algorithm could be modified or replaced to automatically produce clusters more appropriate for sales people. Finally, domain knowledge was used to balance the number of cuisines in a territory with the number of restaurants. Future versions of this project could capture the relevant domain knowledge and perform this step automatically.


<a name="acknowledgements"></a>
# 7. Acknowledgements

Data in this analysis appears courtesy of Foursquare and its admirable commitment to providing free access to students and individual users. I would also like to thank RestaurantSupply.com of Tempe, Arizona and their inside sales team, which gave me a very valuable overview of the sales process in the restaurant industry. Their help made this a more enjoyable and educational experience for me, but of course any mistakes in the scenario or the project’s conclusions are entirely my own.


James Cage

July 9, 2019

# Database Freeze as of July 9, 2019
Locking database as of this date for report generation. J Cage

In [12]:
df_venues = pd.read_csv('https://github.com/JamesDCage/Coursera_Capstone/raw/master/venues.csv')
df_venues.shape

# Should be 4386

(4386, 5)

In [13]:
import pickle
with open ('query', 'rb') as fp:
    query_list = pickle.load(fp)
    
print(len(query_list))
query_list[0:5]

# Should be 135

135


[(((30.357851, -85.605165), (31.131652333333335, -84.6520778)), 8),
 (((30.357851, -84.6520778), (30.551301333333335, -84.413806)), 1),
 (((30.357851, -84.413806), (30.551301333333335, -84.17553419999999)), 99),
 (((30.551301333333335, -84.6520778), (30.744751666666666, -84.413806)), 5),
 (((30.551301333333335, -84.413806), (30.744751666666666, -84.17553419999999)),
  4)]

In [0]:
# SAVE VENUES
file_contents = df_venues.to_csv(index=False)
with(open('venues.csv', 'w')) as file1:
    file1.write(file_contents)

In [0]:
# SAVE QUERIES
# Save query list as pickle file.

import pickle

with open('query', 'wb') as fp:
    pickle.dump(query_list, fp)
    
